In [3]:
pip install opencv-python

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [4]:
import cv2
import os
import numpy as np
from keras.preprocessing.image import img_to_array 
from sklearn.preprocessing import LabelBinarizer
import pickle

In [5]:
EPOCHS = 35
INIT_LR = 1e-3
BS = 32
default_image_size = tuple((100,100))
image_size = 0
directory_root  = 'D:\\arsha\\DL\\Plant Disease Project DL\\plantvillage dataset'
width=100
height=100
depth=3

In [6]:
listdir=(directory_root )

In [7]:
def convert_image_to_array(image_dir):
    try:
        image = cv2.imread(image_dir)
        if image is None:
            print(f"Failed to load image: {image_dir}")
            return np.array([])  # Return an empty array if image is None
        else:
            print(f"Successfully loaded image: {image_dir}")
            print(f"Image shape: {image.shape}")  # Check the shape of the loaded image
            image = cv2.resize(image, default_image_size)
            print(f"Resized image shape: {image.shape}")  # Check the shape after resizing
            return img_to_array(image)
    except Exception as e:
        print(f"Error in converting image {image_dir}: {e}")
        return None


In [8]:
# Load images and labels
image_list, label_list = [], []
try:
    print("[INFO] Loading images ...")
    # List directories inside the root directory
    root_dir = os.listdir(directory_root)
    
    # Remove .DS_Store if present
    if ".DS_Store" in root_dir:
        root_dir.remove(".DS_Store")
    
    # Loop through each folder (representing plant diseases)
    for plant_folder in root_dir:
        plant_disease_folder_list = os.listdir(f"{directory_root}/{plant_folder}")
        
        # Remove .DS_Store from disease folder list if present
        if ".DS_Store" in plant_disease_folder_list:
            plant_disease_folder_list.remove(".DS_Store")
        
        # Process each disease folder
        for plant_disease_folder in plant_disease_folder_list:
            print(f"[INFO] Processing {plant_disease_folder} ...")
            plant_disease_image_list = os.listdir(f"{directory_root}/{plant_folder}/{plant_disease_folder}/")
            
            # Remove .DS_Store from image list if present
            if ".DS_Store" in plant_disease_image_list:
                plant_disease_image_list.remove(".DS_Store")
            
            # Process images (limit to first 250 images)
            for image in plant_disease_image_list[:250]:
                image_directory = f"{directory_root}/{plant_folder}/{plant_disease_folder}/{image}"
                # Check for .jpg or .JPG images
                if image_directory.endswith(".jpg") or image_directory.endswith(".JPG"):
                    image_array = convert_image_to_array(image_directory)
                    if image_array is not None and image_array.size > 0:
                        image_list.append(image_array)
                        label_list.append(plant_disease_folder)
    
    print("[INFO] Image loading completed")

except Exception as e:
    print(f"Error: {e}")


[INFO] Loading images ...
[INFO] Processing Apple___Apple_scab ...
Successfully loaded image: D:\arsha\DL\Plant Disease Project DL\plantvillage dataset/color/Apple___Apple_scab/00075aa8-d81a-4184-8541-b692b78d398a___FREC_Scab 3335.JPG
Image shape: (224, 224, 3)
Resized image shape: (100, 100, 3)
Successfully loaded image: D:\arsha\DL\Plant Disease Project DL\plantvillage dataset/color/Apple___Apple_scab/01a66316-0e98-4d3b-a56f-d78752cd043f___FREC_Scab 3003.JPG
Image shape: (224, 224, 3)
Resized image shape: (100, 100, 3)
Successfully loaded image: D:\arsha\DL\Plant Disease Project DL\plantvillage dataset/color/Apple___Apple_scab/01f3deaa-6143-4b6c-9c22-620a46d8be04___FREC_Scab 3112.JPG
Image shape: (224, 224, 3)
Resized image shape: (100, 100, 3)
Successfully loaded image: D:\arsha\DL\Plant Disease Project DL\plantvillage dataset/color/Apple___Apple_scab/0208f4eb-45a4-4399-904e-989ac2c6257c___FREC_Scab 3037.JPG
Image shape: (224, 224, 3)
Resized image shape: (100, 100, 3)
Successfully 

In [9]:
image_size = len(image_list)

In [10]:
print(image_size)

24456


In [11]:
print(label_list[:10])  # Check the first 10 labels


['Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab', 'Apple___Apple_scab']


In [12]:
label_binarizer = LabelBinarizer()
image_labels = label_binarizer.fit_transform(label_list)
pickle.dump(label_binarizer,open('label_transform.pkl', 'wb'))
n_classes = len(label_binarizer.classes_)


In [13]:
print(label_binarizer.classes_)

['Apple___Apple_scab' 'Apple___Black_rot' 'Apple___Cedar_apple_rust'
 'Apple___healthy' 'Blueberry___healthy'
 'Cherry_(including_sour)___Powdery_mildew'
 'Cherry_(including_sour)___healthy'
 'Corn_(maize)___Cercospora_leaf_spot Gray_leaf_spot'
 'Corn_(maize)___Common_rust_' 'Corn_(maize)___Northern_Leaf_Blight'
 'Corn_(maize)___healthy' 'Grape___Black_rot'
 'Grape___Esca_(Black_Measles)'
 'Grape___Leaf_blight_(Isariopsis_Leaf_Spot)' 'Grape___healthy'
 'Orange___Haunglongbing_(Citrus_greening)' 'Peach___Bacterial_spot'
 'Peach___healthy' 'Pepper,_bell___Bacterial_spot'
 'Pepper,_bell___healthy' 'Potato___Early_blight' 'Potato___Late_blight'
 'Potato___healthy' 'Raspberry___healthy' 'Soybean___healthy'
 'Squash___Powdery_mildew' 'Strawberry___Leaf_scorch'
 'Strawberry___healthy' 'Tomato___Bacterial_spot' 'Tomato___Early_blight'
 'Tomato___Late_blight' 'Tomato___Leaf_Mold' 'Tomato___Septoria_leaf_spot'
 'Tomato___Spider_mites Two-spotted_spider_mite' 'Tomato___Target_Spot'
 'Tomato___Tom

In [14]:
np_image_list = np.array(image_list, dtype=np.float16) / 225.0

In [15]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(np_image_list, image_labels, test_size=0.2, random_state = 42) 
print("[INFO] Spliting data to train, test")

[INFO] Spliting data to train, test


In [16]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator
aug = ImageDataGenerator(
    rotation_range=25, width_shift_range=0.1,
    height_shift_range=0.1, shear_range=0.2, 
    zoom_range=0.2,horizontal_flip=True, 
    fill_mode="nearest")

In [17]:
from keras.models import Sequential
from keras.layers import Dense,Activation,Flatten,Dropout
from keras.layers import Conv2D,MaxPooling2D
from keras.callbacks import ModelCheckpoint
from tensorflow.keras.layers import BatchNormalization
from keras import backend as K

In [18]:
model = Sequential()
inputShape = (height, width, depth)
chanDim = -1
if K.image_data_format() == "channels_first":
    inputShape = (depth, height, width)
    chanDim = 1
model.add(Conv2D(32, (3, 3), padding="same",input_shape=inputShape))
model.add(Activation("relu"))
model.add(BatchNormalization(axis=chanDim))
model.add(MaxPooling2D(pool_size=(3, 3)))
model.add(Dropout(0.25))
model.add(Conv2D(64, (3, 3), padding="same"))
model.add(Activation("relu"))
model.add(BatchNormalization(axis=chanDim))
model.add(Conv2D(64, (3, 3), padding="same"))
model.add(Activation("relu"))
model.add(BatchNormalization(axis=chanDim))
model.add(Conv2D(64, (3, 3), padding="same"))
model.add(Activation("relu"))
model.add(BatchNormalization(axis=chanDim))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))
model.add(Conv2D(128, (3, 3), padding="same"))
model.add(Activation("relu"))
model.add(BatchNormalization(axis=chanDim))
model.add(Conv2D(128, (3, 3), padding="same"))
model.add(Activation("relu"))
model.add(BatchNormalization(axis=chanDim))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(1024))
model.add(Activation("relu"))
model.add(BatchNormalization())
model.add(Dropout(0.5))
model.add(Dense(n_classes))
model.add(Activation("softmax"))

C:\Users\sagar\AppData\Roaming\Python\Python310\site-packages\keras\src\layers\convolutional\base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [19]:
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv2d (Conv2D)                 │ (None, 100, 100, 32)   │           896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation (Activation)         │ (None, 100, 100, 32)   │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 100, 100, 32)   │           128 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d (MaxPooling2D)    │ (None, 33, 33, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 33, 33, 32)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_1 (Conv2D)               │ (None, 33, 33, 64)     │        18,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_1 (Activation)       │ (None, 33, 33, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 33, 33, 64)     │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_2 (Conv2D)               │ (None, 33, 33, 64)     │        36,928 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_2 (Activation)       │ (None, 33, 33, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 33, 33, 64)     │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_3 (Conv2D)               │ (None, 33, 33, 64)     │        36,928 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_3 (Activation)       │ (None, 33, 33, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_3           │ (None, 33, 33, 64)     │           256 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ max_pooling2d_1 (MaxPooling2D)  │ (None, 16, 16, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 16, 16, 64)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_4 (Conv2D)               │ (None, 16, 16, 128)    │        73,856 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_4 (Activation)       │ (None, 16, 16, 128)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_4           │ (None, 16, 16, 128)    │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ conv2d_5 (Conv2D)               │ (None, 16, 16, 128)    │       147,584 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_5 (Activation)       │ (None, 16, 16, 128)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_5           │ (None, 16, 16, 128)    │           512 │
│ (BatchNormalization)            │                        │             

 Total params: 8,749,286 (33.38 MB)

 Trainable params: 8,746,278 (33.36 MB)

 Non-trainable params: 3,008 (11.75 KB)

In [20]:
from tensorflow.keras.optimizers import Adam

# Compiling Model
opt = Adam(learning_rate=INIT_LR, decay=INIT_LR / EPOCHS)

# Distribution
model.compile(loss="binary_crossentropy", optimizer=opt, metrics=["accuracy"])

# Train the network
print("[INFO] training network...")


[INFO] training network...


C:\Users\sagar\AppData\Roaming\Python\Python310\site-packages\keras\src\optimizers\base_optimizer.py:86: UserWarning: Argument `decay` is no longer supported and will be ignored.
  warnings.warn(


In [21]:
# Fitting Model
history = model.fit(
    aug.flow(x_train, y_train, batch_size=BS),
    validation_data=(x_test, y_test),
    steps_per_epoch=len(x_train) // BS,
    epochs=EPOCHS,
    verbose=1
)

C:\Users\sagar\AppData\Roaming\Python\Python310\site-packages\keras\src\trainers\data_adapters\py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


Epoch 1/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 194s 310ms/step - accuracy: 0.1047 - loss: 0.3699 - val_accuracy: 0.2664 - val_loss: 0.1008
Epoch 2/35
  1/611 ━━━━━━━━━━━━━━━━━━━━ 2:48 276ms/step - accuracy: 0.4062 - loss: 0.0925

C:\Users\sagar\AppData\Roaming\Python\Python310\site-packages\keras\src\trainers\epoch_iterator.py:107: UserWarning: Your input ran out of data; interrupting training. Make sure that your dataset or generator can generate at least `steps_per_epoch * epochs` batches. You may need to use the `.repeat()` function when building your dataset.
  self._interrupted_warning()


611/611 ━━━━━━━━━━━━━━━━━━━━ 8s 13ms/step - accuracy: 0.4062 - loss: 0.0925 - val_accuracy: 0.2608 - val_loss: 0.1171
Epoch 3/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 180s 294ms/step - accuracy: 0.3859 - loss: 0.0884 - val_accuracy: 0.4315 - val_loss: 0.0848
Epoch 4/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 8s 13ms/step - accuracy: 0.5625 - loss: 0.0709 - val_accuracy: 0.4172 - val_loss: 0.0863
Epoch 5/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 183s 300ms/step - accuracy: 0.5177 - loss: 0.0707 - val_accuracy: 0.4426 - val_loss: 0.0862
Epoch 6/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 8s 12ms/step - accuracy: 0.6562 - loss: 0.0594 - val_accuracy: 0.4387 - val_loss: 0.0876
Epoch 7/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 171s 279ms/step - accuracy: 0.5957 - loss: 0.0592 - val_accuracy: 0.4162 - val_loss: 0.0875
Epoch 8/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 7s 12ms/step - accuracy: 0.6562 - loss: 0.0507 - val_accuracy: 0.4156 - val_loss: 0.0880
Epoch 9/35
611/611 ━━━━━━━━━━━━━━━━━━━━ 165s 271ms/step - accuracy: 0.6347 - loss: 0.0543 - val_acc

In [22]:
print("[INFO] Calculating model accuracy")
scores = model.evaluate(x_test, y_test)
print(f"Test Accuracy: {scores[1]*100}")

[INFO] Calculating model accuracy
153/153 ━━━━━━━━━━━━━━━━━━━━ 7s 43ms/step - accuracy: 0.8205 - loss: 0.0318
Test Accuracy: 81.84791207313538


In [23]:
# Save the model using TensorFlow SavedModel format
model.save('plant_disease.h5')

In [24]:
scores = model.evaluate(x_train, y_train)
print(f"Training Accuracy: {scores[1]*100}")

612/612 ━━━━━━━━━━━━━━━━━━━━ 28s 45ms/step - accuracy: 0.8458 - loss: 0.0268
Training Accuracy: 84.6912682056427
